- Load Kalman Data
- Load Video
- Align Timestamps\
- align "0" distance from ground plane on kalman\
- For each frame in video, let POS = closest kalman timestep\
- project points from "depth" where depth is render of ground plane - to test this, produce video of ground plane from phone orientation\
- rotate pointcloud and render from above
- use SIFT to transform it into relative position of first image



In [1]:
import os
import cv2
import numpy as np
import cupy as cp
from ultralytics import YOLO
import matplotlib.pyplot as plt
import sys
from PIL import Image
from importlib import reload
import pandas as pd
import plotly.express as px
import gdown
import zipfile

sys.path.insert(1, '..')
os.environ["OPENCV_IO_ENABLE_OPENEXR"] = "1"

In [2]:
files = {
    'walk_to_malachowski' : 'https://drive.google.com/file/d/1EejwRl80fnWIlh9l_YjYTrjQb3d7mMSR/view?usp=drive_link',
    'walk_down_parking_lot' : 'https://drive.google.com/file/d/1RtRjmR7ggn5DgyxNK6mGkihZY-g9NyCq/view?usp=drive_link',
    'malachowski_chamomile' : 'https://drive.google.com/file/d/1V28HPGOMnI-l-GiAFGB5xzt0YajLtwMU/view?usp=drive_link',
    'malachowski_chamomile_2' : 'https://drive.google.com/file/d/1JD9SI-bM44BPeG2frwaznO2Fq97BAmUM/view?usp=drive_link',
    'first_test_walk' : 'https://drive.google.com/file/d/1u7FCFc4uaZscHvZ6wH9wU2pb_Mz9djPF/view?usp=drive_link'
}

def convert_to_direct_download(gdrive_link):
    start = gdrive_link.find('/d/') + 3
    end = gdrive_link.find('/view', start)
    file_id = gdrive_link[start:end]

    direct_download_url = f'https://drive.google.com/uc?id={file_id}&export=download'

    return direct_download_url

In [3]:
# @title Selected File
selected = "walk_to_malachowski" # @param ["malachowski_chamomile", "malachowski_chamomile_2", "walk_to_malachowski", "first_test_walk", "walk_down_parking_lot"]

url = convert_to_direct_download(files[selected])
gdown.download(url, "of.zip")
with zipfile.ZipFile("./of.zip", 'r') as zip_ref:
    zip_ref.extractall("../Data/")

Downloading...
From (original): https://drive.google.com/uc?id=1EejwRl80fnWIlh9l_YjYTrjQb3d7mMSR&export=download
From (redirected): https://drive.google.com/uc?id=1EejwRl80fnWIlh9l_YjYTrjQb3d7mMSR&export=download&confirm=t&uuid=bc993b8a-7021-4ed6-a330-538aa6f51fd3
To: c:\Users\c1a55\Documents\Roborouter\Notebooks\of.zip
100%|██████████| 536M/536M [00:07<00:00, 72.4MB/s] 


In [4]:
%cd ../data/
%cd $selected

c:\Users\c1a55\Documents\Roborouter\data
c:\Users\c1a55\Documents\Roborouter\data\walk_to_malachowski


In [57]:
AccelerometerDF = pd.read_csv('Accelerometer.csv')
#zyx

BarometerDF = pd.read_csv('Barometer.csv')
#relativeAltitude
#pressure

#Highly prefused, but not with accel or baro
LocationDF = pd.read_csv('Location.csv')
#altitude
#speedAccuracy
#bearingAccuracy
#latitude
#altitudeAboveMeanSaLevel
#bearing
#horizontalAccuracy
#verticalAccuracy
#longitude
#speed

#Don't care, prefused into orientation
#MagnetometerDF = pd.read_csv('Magnetometer.csv')
#zyx

#To be used for synchronization
MicrophoneDF = pd.read_csv('Microphone.csv')
#dBFS

#Prefused = best guess. Smoothing welcomed.
OrientationDF = pd.read_csv('Orientation.csv')
#yaw
#qx
#qz
#roll
#qw
#qy
#pitch
AccelerometerDF.head()

time  seconds_elapsed         z         y         x
0  1707585936836849400         0.120849 -1.105513  0.109932 -0.172708
1  1707585936846874400         0.130874 -0.984158  0.009005 -0.031572
2  1707585936856900400         0.140900 -0.622699 -0.213101  0.081729
3  1707585936866925600         0.150926 -0.113919 -0.439512  0.044241
4  1707585936876950500         0.160950  0.339074 -0.531960  0.010381

In [53]:
from scipy.spatial.transform import Rotation as R
pi = np.pi

def convert_xyz_acceleration_to_NEU(ax, ay, az, qx, qy, qz, qw):
  Rquat = R.from_quat([qx, qy, qz, qw])
  rotation_matrix = Rquat.as_matrix()
  inv = rotation_matrix.T
  result = inv @ [ax, ay, az]
  return result


In [60]:
#Preprocessing the accelerations into ENU accelerations using the phone rotation:

from turtle import position


def convert_accelerations(accel_df, orient_df):
    # Initialize an empty DataFrame to store the converted accelerations
    converted_accelerations = pd.DataFrame(accel_df)
    converted_accelerations.drop(axis='columns', columns=['time', 'seconds_elapsed'], inplace=True)
    converted_accelerations.rename(
        mapper = {'z':'east', 'y':'north', 'x':'up'},
        axis='columns',
        inplace=True
    )

    for i in range(len(accel_df)):
        # Create a rotation object from the roll, pitch, and yaw

        ax = accel_df.iloc[i]["x"]
        ay = accel_df.iloc[i]["y"]
        az = accel_df.iloc[i]["z"]


        qw = orient_df.iloc[i]["qw"]
        qx = orient_df.iloc[i]["qx"]
        qy = orient_df.iloc[i]["qy"]
        qz = orient_df.iloc[i]["qz"]

        # Apply the rotation to the acceleration vector
        north, east, up = convert_xyz_acceleration_to_NEU(ax, ay, az, qx, qy, qz, qw)

        # Append the converted acceleration to the DataFrame
        converted_accelerations.iloc[i] = [east, north, up]

    return converted_accelerations

def integrate_acceleration_to_position(accel_df, delta_t=1):
    velocity_df = pd.DataFrame(np.zeros_like(accel_df.values), columns=['east', 'north', 'up'])
    position_df = pd.DataFrame(np.zeros_like(accel_df.values), columns=['east', 'north', 'up'])

    # Integrate acceleration to get velocity and position
    for i in range(1, len(accel_df)):
        velocity_df.iloc[i] = velocity_df.iloc[i - 1] + accel_df.iloc[i]
        position_df.iloc[i] = position_df.iloc[i - 1] + velocity_df.iloc[i] * delta_t
        print(accel_df.iloc[i]);
        print(velocity_df.iloc[i])
        print(position_df.iloc[i])

    return position_df

ENUAccelDF = convert_accelerations(AccelerometerDF, OrientationDF)
int_location_df = integrate_acceleration_to_position(ENUAccelDF, .01026)

fig = px.line_3d(
    int_location_df,
    x=int_location_df['north'],
    y=int_location_df['east'],
    z=int_location_df['up']
)
fig.show()

east    -0.096927
north   -0.124329
up      -0.972004
Name: 1, dtype: float64
east    -0.000994
north   -0.001276
up      -0.009973
Name: 1, dtype: float64
east    -0.294123
north   -0.001112
up      -1.593113
Name: 2, dtype: float64
east    -0.004012
north   -0.001287
up      -0.026318
Name: 2, dtype: float64
east    -0.655314
north    0.257642
up      -1.696523
Name: 3, dtype: float64
east    -0.010736
north    0.001356
up      -0.043724
Name: 3, dtype: float64
east    -1.066926
north    0.578568
up      -1.342063
Name: 4, dtype: float64
east    -0.021682
north    0.007292
up      -0.057494
Name: 4, dtype: float64
east    -1.504979
north    0.924137
up      -0.781065
Name: 5, dtype: float64
east    -0.037123
north    0.016774
up      -0.065508
Name: 5, dtype: float64
east    -2.053408
north    1.137655
up      -0.308756
Name: 6, dtype: float64
east    -0.058191
north    0.028446
up      -0.068676
Name: 6, dtype: float64
east    -2.600288
north    1.186206
up       0.045079
Name: 7, d

In [20]:
import pymap3d as pm
# The local coordinate origin (Zermatt, Switzerland)
lat0 = LocationDF["latitude"][0] # deg
lon0 = LocationDF["longitude"][0]  # deg
h0 = LocationDF["altitude"][0]     # meters

def convert_to_enu(row):
    east, north, up = pm.geodetic2enu(row['latitude'], row['longitude'], row['altitude'], lat0, lon0, h0)
    return pd.Series([east, north, up])

# Apply the function to each row and create new columns
ENULocDF=pd.DataFrame()
ENULocDF[['east', 'north', 'up']] = LocationDF.apply(convert_to_enu, axis=1)

In [21]:
# for creating a responsive plot
fig = px.line_3d(ENULocDF, x=ENULocDF['north'], y=ENULocDF['east'], z=ENULocDF['up'])
fig.show()

In [50]:
import numpy as np
delta_t = 1/100  # Time step for 100Hz frequency
initial_state = np.zeros(6)  # [east_pos, north_pos, up_pos, east_vel, north_vel, up_vel]
transition_matrix = np.array([
    [1, 0, 0, delta_t, 0, 0],
    [0, 1, 0, 0, delta_t, 0],
    [0, 0, 1, 0, 0, delta_t],
    [0, 0, 0, 1, 0, 0],
    [0, 0, 0, 0, 1, 0],
    [0, 0, 0, 0, 0, 1]
])

state_covariance = np.eye(6) * 100
state_covariance_combined = np.eye(6) * 100
process_noise = np.eye(6) * 0.01 

average_acceleration = ENUAccelDF[['east', 'north', 'up']].abs().mean()
measurement_noise_accel = np.array([
    [average_acceleration['east']*0, 0, 0], #Iphone docs say 1% measurement error. We crank artificially
    [0, average_acceleration['north']*0, 0],
    [0, 0, average_acceleration['up']*0],
])
measurement_noise_gps = np.eye(3) * 3  # GPS measurement noise
observation_matrix_accel = np.array([
    [0, 0, 0, 1, 0, 0],  # east_pos
    [0, 0, 0, 0, 1, 0],  # north_pos
    [0, 0, 0, 0, 0, 1],  # up_pos
])

observation_matrix_gps = np.array([
    [1, 0, 0],
    [0, 1, 0],
    [0, 0, 1]
])

measurement_noise_combined = np.block([
    [measurement_noise_gps, np.zeros((3, 3))],
    [np.zeros((3, 3)), measurement_noise_accel]
])

observation_matrix_combined = np.block([
    [observation_matrix_gps, np.zeros((3, 3))],
    [np.zeros((3, 3)), np.array([
        [1, 0, 0],
        [0, 1, 0],
        [0, 0, 1],
        ])
     ]
])

state = np.zeros(6)

dict = {'east':[], 'north':[], 'up':[]}
outputCoords = pd.DataFrame(dict)
print(ENUAccelDF.shape)
# Kalman filter loop
for index, accel_row in enumerate(zip(ENUAccelDF.iterrows())):
    # Update state and state covariance here based on the transition matrix and process noise
    state = transition_matrix.dot(state)
    state_covariance = transition_matrix.dot(state_covariance).dot(transition_matrix.T) + process_noise

    if index % 100 == 0:
      # GPS data is available
        try:
            loc_row = ENULocDF.iloc[index // 100]
        except Exception as e:
            print(e)
            break
        observation_vector = np.concatenate((np.array([loc_row['east'], loc_row['north'], loc_row['up']]), np.array([accel_row[0][1]['east'], accel_row[0][1]['north'], accel_row[0][1]['up']])))
        observation_matrix = observation_matrix_combined
        measurement_noise = measurement_noise_combined
        S = observation_matrix.dot(state_covariance).dot(observation_matrix.T) + measurement_noise  # 6x6 matrix
        K = state_covariance.dot(observation_matrix.T).dot(np.linalg.inv(S))  # K will be 6x6
    else:
        # Only accelerometer data is available
        observation_vector = np.array([accel_row[0][1]['east'], accel_row[0][1]['north'], accel_row[0][1]['up']])
        observation_matrix = observation_matrix_accel
        measurement_noise = measurement_noise_accel

        S = observation_matrix.dot(state_covariance).dot(observation_matrix.T) + measurement_noise  # 3x3 matrix for accel
        K = state_covariance.dot(observation_matrix.T).dot(np.linalg.inv(S))  # K will be 6x3 for accel


    state = state + K.dot(observation_vector - observation_matrix.dot(state))

    # Update state covariance
    state_covariance = (np.eye(len(state)) - K.dot(observation_matrix)).dot(state_covariance)

    outputCoords.loc[len(outputCoords.index)] = state[0:3]

(15727, 3)


In [51]:
# Add a 'source' column to each DataFrame to distinguish them in the plot
ENULocDF['source'] = 'GPS'
outputCoords['source'] = 'Kalman Filter'

# Combine the two DataFrames
combined_df = pd.concat([ENULocDF.rename(columns={'east': 'Y', 'north': 'X', 'up': 'Z'}),
                         outputCoords.rename(columns={'east': 'Y', 'north': 'X', 'up': 'Z'})])

# Plot using Plotly Express
fig = px.line_3d(combined_df, x='X', y='Y', z='Z', color='source')
fig.layout.scene.aspectmode='data'
fig.show()

In [31]:
print(outputCoords.head(5)) #east north up source
print(OrientationDF.head(5))

print(outputCoords.shape)
print(OrientationDF.shape)




       east     north        up         source
0 -0.000026 -0.000090 -0.000314  Kalman Filter
1 -0.000955 -0.002554 -0.010679  Kalman Filter
2 -0.002318 -0.003251 -0.019078  Kalman Filter
3 -0.004723 -0.002218 -0.023902  Kalman Filter
4 -0.008048  0.000018 -0.024566  Kalman Filter
                  time  seconds_elapsed       yaw        qx        qz  \
0  1707585936836849400         0.120849 -0.543345 -0.028643  0.269779   
1  1707585936846874400         0.130874 -0.545215 -0.030435  0.270720   
2  1707585936856900400         0.140900 -0.547201 -0.032495  0.271718   
3  1707585936866925600         0.150926 -0.549221 -0.034340  0.272721   
4  1707585936876950500         0.160950 -0.551121 -0.035765  0.273654   

       roll        qw        qy     pitch  
0 -0.096052 -0.960761  0.057768  0.086314  
1 -0.094900 -0.960445  0.057710  0.089830  
2 -0.093506 -0.960102  0.057607  0.093840  
3 -0.092129 -0.959762  0.057459  0.097411  
4 -0.090964 -0.959453  0.057302  0.100158  
(1590, 4)
(1572